<div class="alert" style="background-color:#fff; color:white; padding:0px 10px; border-radius:5px;"><h1 style='margin:15px 15px; color:#006a79; font-size:40px'>Customer Account Identification through Demographics</h1>
</div>

In [1]:
# Importing all required libraries

import numpy as np
import pandas as pd

from sklearn.preprocessing import LabelEncoder
from sklearn.cluster import KMeans
from itertools import permutations, combinations
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import FunctionTransformer
from sklearn.pipeline import FeatureUnion, Pipeline

import matplotlib.pyplot as plt
import json
import nltk
import re
%matplotlib inline
import seaborn as sns

import unicodedata
from metaphone import doublemetaphone
from enum import Enum

<div class="alert alert-info" style="background-color:#006a79; color:white; padding:0px 10px; border-radius:5px;"><h2 style='margin:10px 5px'>User Defined Functions</h2>
</div>

In [2]:
# Identify null values for all the columns in dataframe

def getNullStats(df):
    tbl_results = []
    print('Total Features(Columns) of dataset = ', len(df.columns))
    total_samples = len(df)
    null_samples = df.isnull().sum()
    tbl_results = pd.concat([null_samples, round(null_samples/total_samples*100, 2)], axis=1)
    tbl_results = tbl_results.rename(columns = {0:'Nulls', 1:'Percent'})
    tbl_results = tbl_results[tbl_results.iloc[:, 1] !=0].sort_values('Nulls', ascending=False).round(2)
    print('Null Features(Columns) of dataset = ', len(tbl_results))
    return tbl_results

In [3]:
# Clearn JSON structure

def clean_json(x):
# Create apply function for decoding JSON
    return json.loads(x) 

In [4]:
# Check if 'subset' is sub set of 'supset'

def isSubset(df, supset, subset):
    # Get max width of subset cell
    # width_subset = int(df[subset].str.encode(encoding='utf-8').str.len().max())
    width_subset = 11
        
    # Get indices of non null rows of subset
    subset_list = df[subset][~df[subset].isnull()].index
    
    df_supset = (df[supset].astype('str')).str[:width_subset][subset_list]
    #print(df_supset)
    
    df_subset = df[subset].str[:width_subset][subset_list]
    #print(df_subset)
    
    return df_supset.equals(df_subset)

In [5]:
def tokenize(subject):
    # tokens = [word.lower() for sent in nltk.sent_tokenize(subject) for word in nltk.word_tokenize(sent)]
    # To eliminate '-' characters in name
    tokens = re.split('[ -]', subject)
    
    filtered_tokens = []
    for token in tokens:
        if re.search('[a-zA-Z]', token) and (len(token) > 1):
            filtered_tokens.append(token)

    return filtered_tokens

In [6]:
def getPermutations(subject, n):
    lstTokens = tokenize(subject)
    lstTuples = list(permutations(lstTokens, n))
    lstItems = []
    lstItems.extend([' '.join(item) for item in lstTuples])
    
    return lstItems

In [7]:
def flat(lst):
    if isinstance(lst, list):
        for item in lst:
            yield from flat(item)
    else:        
        yield lst

In [8]:
def getAllPermutations(subject):
    lstItems = []
    final = []

    tokens = tokenize(subject)
    subject_length_words = len(tokens)
    lstItems.extend(getPermutations(subject, int(i+1)) for i in np.arange(int(subject_length_words)))
    
    final.append([item for item in lstItems])
    return list(flat(final))

In [9]:
def kMeansClustering(tfidf_mat, nClusters, rnd_state=9):
    km = KMeans(n_clusters=nClusters, random_state=rnd_state)
    %time km.fit(tfidf_mat)
    clusters = km.labels_.tolist()
    return km

In [10]:
def getMailIDs(subject):
    mail_id = ''
    mailer = subject.split('@')[0]
    
    mail_id = "".join(re.split("[^a-zA-Z]*", mailer))
    return mail_id

In [11]:
def Vectorize(dataframe, feature, useIdf):
    vectorizer = TfidfVectorizer(useIdf)
    matrix = vectorizer.fit_transform(dataframe[feature])

    features = vectorizer.get_feature_names()
    corpus = [n for n in dataframe[feature]]
    df_feature = pd.DataFrame(matrix.todense(), index=corpus, columns=features)

    print('Shape of the matrix =>', matrix.shape)
    print('No. of Features =>', len(features))
    print('No. of documents =>', len(corpus))

    return (matrix, df_feature)

In [12]:
class Threshold(Enum):
    WEAK = 0
    NORMAL = 1
    STRONG = 2

In [13]:
""" Normalise (normalize) unicode data in Python to remove umlauts, accents etc. """
def normalize_unicode_to_ascii(data):

    normal = unicodedata.normalize('NFKD', data).encode('ASCII', 'ignore')
    val = normal.decode("utf-8")
    val = val.lower()
    # remove special characters
    val = re.sub('[^A-Za-z0-9 ]+', ' ', val)
    # remove multiple spaces
    val = re.sub(' +', ' ', val)
    return val

In [14]:
def sort_words(words):
    words = words.split(" ")
    words.sort()
    newSentence = " ".join(words)
    return newSentence

In [15]:
def double_metaphone(value):
    return doublemetaphone(value)

In [16]:
# #(Primary Key = Primary Key) = Strongest Match
# #(Secondary Key = Primary Key) = Normal Match
# #(Primary Key = Secondary Key) = Normal Match
# #(Alternate Key = Alternate Key) = Minimal Match
# def double_metaphone_compare(tuple1,tuple2,threshold):
#     if threshold == Threshold.WEAK:
#         if tuple1[1] == tuple2[1]:
#             return True
#     elif threshold == Threshold.NORMAL:
#         if tuple1[0] == tuple2[1] or tuple1[1] == tuple2[0]:
#             return True
#     else:
#         if tuple1[0] == tuple2[0]:
#             return True
#     return False

In [17]:
from nameparser import HumanName

def cleanHumanName(subject):
    name = HumanName(subject)
    cleaned_name = name.first + ' ' + name.middle + ' ' + name.last
    return re.sub(' +', ' ', cleaned_name)

In [18]:
import warnings
warnings.filterwarnings("ignore")

In [19]:
# pd.set_option('display.max_columns', None)
# pd.set_option('display.min_rows', 130)
# pd.set_option('display.max_rows', None)
# pd.set_option('display.width', 10000)
pd.set_option('display.max_colwidth', 0)

In [20]:
# Read customer data
dm_df = pd.read_csv('cust360_customer_demographics_linked_1000.csv',  sep='|')

# Include header in the dataframe
dm_df.columns=[
    'cust_id', 'acct_id', 'cm11', 'cm13', 'cm15', 'alt_acct_id', 'parnt_acct_no', 'mbr_rwrd_id',
    'setup_refer_acct_id', 'emb_indv_nm', 'emb_prcs_indv_nm', 'indv_prim_ttl_nm',
    'indv_prim_pfx_nm', 'indv_prim_first_nm', 'indv_prim_mid_nm', 'indv_prim_lst_nm',
    'indv_prim_suff_nm', 'indv_prim_add_lst_nm', 'indv_prim_full_nm', 'indv_prim_prcs_full_nm',
    'indv_prim_prcs_first_nm', 'indv_prim_prcs_mid_nm', 'indv_prim_prcs_lst_nm', 'indv_scnd_nm',
    'lgl_nm', 'lgl_prcs_nm', 'gend_cd', 'cust_dob', 'birth_yr', 'prcs_dob', 'gov_doc_id',
    'ad_home_line_care', 'ad_home_st_line1', 'ad_home_st_line2', 'ad_home_st_line3',
    'ad_home_st_line4', 'ad_home_prcs_st_line1', 'ad_home_prcs_st_line2',
    'ad_home_prcs_st_line3', 'ad_home_prcs_st_line4', 'ad_home_geo_coord_latd',
    'ad_home_geo_coord_longt', 'ad_bus_line_care', 'ad_bus_st_line1', 'ad_bus_st_line2',
    'ad_bus_st_line3', 'ad_bus_st_line4', 'ad_bus_prcs_st_line1', 'ad_bus_prcs_st_line2',
    'ad_bus_prcs_st_line3', 'ad_bus_prcs_st_line4', 'ad_bus_geo_coord_latd',
    'ad_bus_geo_coord_longt', 'ad_alt_line_care', 'ad_alt_st_line1', 'ad_alt_st_line2',
    'ad_alt_st_line3', 'ad_alt_st_line4', 'ad_alt_prcs_st_line1', 'ad_alt_prcs_st_line2',
    'ad_alt_prcs_st_line3', 'ad_alt_prcs_st_line4', 'ad_alt_geo_coord_latd',
    'ad_alt_geo_coord_longt', 'ad_temp_line_care', 'ad_temp_st_line1', 'ad_temp_st_line2',
    'ad_temp_st_line3', 'ad_temp_st_line4', 'ad_temp_prcs_st_line1', 'ad_temp_prcs_st_line2',
    'ad_temp_prcs_st_line3', 'ad_temp_prcs_st_line4', 'ad_temp_geo_coord_latd',
    'ad_temp_geo_coord_longt', 'ad_other_line_care', 'ad_other_st_line1', 'ad_other_st_line2',
    'ad_other_st_line3', 'ad_other_st_line4', 'ad_other_prcs_st_line1', 'ad_other_prcs_st_line2',
    'ad_other_prcs_st_line3', 'ad_other_prcs_st_line4', 'ad_other_geo_coord_latd',
    'ad_other_geo_coord_longt', 'ad_add', 'home_phone_no', 'home_prcs_phone_no',
    'home_prcs_full_phone_no', 'alt_home_phone_no', 'alt_home_prcs_phone_no',
    'alt_home_prcs_full_phone_no', 'bus_phone_no', 'bus_prcs_phone_no',
    'bus_prcs_full_phone_no', 'alt_bus_phone_no', 'alt_bus_prcs_phone_no',
    'alt_bus_prcs_full_phone_no', 'mob_phone_no', 'mob_prcs_phone_no', 'mob_prcs_full_phone_no',
    'alt_mob_phone_no', 'alt_mob_prcs_phone_no', 'alt_mob_prcs_full_phone_no',
    'atty_phone_no', 'atty_prcs_phone_no', 'atty_prcs_full_phone_no', 'fax_no', 'prcs_fax_no',
    'prcs_full_fax_no', 'phone_ani', 'other_phone_no', 'other_prcs_phone_no',
    'other_prcs_full_phone_no', 'add_phone', 'srvc_email_ad', 'srvc_prcs_email_ad',
    'estmt_email_ad', 'estmt_prcs_email_ad', 'other_email_ad', 'bank_prim_acct_no',
    'bank_prim_rte_no', 'bank_prim_iban_no', 'bank_scnd_acct_no', 'bank_scnd_rte_no',
    'bank_scnd_iban_no'
]
dm_df.head()

cust_id        acct_id         cm11           cm13             cm15  \
0  600125815019  25190699       \N           \N             \N                
1  568709454017  975879         \N           \N             \N                
2  360534588017  3727271315801  37272713158  3727271315801  372727131581017   
3  196410570010  14884816       \N           \N             \N                
4  35442548013   3798238830600  37982388306  3798238830600  379823883061002   

  alt_acct_id  parnt_acct_no mbr_rwrd_id setup_refer_acct_id  \
0  \N          \N             \N          24782279             
1  \N          \N             \N          975879               
2  \N          3727271315800  \N          3713000280900        
3  \N          \N             \N          12709897             
4  \N          \N             \N          \N                   

          emb_indv_nm  ... srvc_prcs_email_ad estmt_email_ad  \
0  \N                  ...  \N                 \N              
1  \N                  ...  \N                 \N              
2  LAURA PALLAS        ...  \N                 \N              
3  \N                  ...  \N                 \N              
4  NARINDER S SAWHNEY  ...  \N                 \N              

  estmt_prcs_email_ad other_email_ad bank_prim_acct_no bank_prim_rte_no  \
0  \N                  \N             \N                \N                
1  \N                  \N             \N                \N                
2  \N                  \N             \N                \N                
3  \N                  \N             \N                \N                
4  \N                  \N             \N                \N                

  bank_prim_iban_no bank_scnd_acct_no bank_scnd_rte_no bank_scnd_iban_no  
0  \N                \N                \N               \N                
1  \N                \N                \N               \N                
2  \N                \N                \N               \N                
3  \N                \N                \N               \N                
4  \N                \N                \N               \N                

[5 rows x 127 columns]

Notice empty cells are filled with \N character, which should be replaced with Nulls. Lets fill with Null as required

In [21]:
# Replacing \N from all cells source data with NaN/Nulls

dm_df.replace('\\N', np.nan, inplace=True)
# dm_df.head()

<font color='#006a79'> **Group independent features/columns based on domain knowledge and cursory glance over data**</font>

Let us group columns based on **Entities** to which they belong as shown below:
- **Customer entity**: 
        'cust_id' (Leave untouched for future use)


- **Account entity**:  
        'acct_id', 'cm11', 'cm13', 'cm15', 'alt_acct_id', 
        'parnt_acct_no', 'mbr_rwrd_id', 'setup_refer_acct_id',
        'bank_prim_acct_no', 'bank_prim_rte_no', 'bank_prim_iban_no',
        'bank_scnd_acct_no', 'bank_scnd_rte_no', 'bank_scnd_iban_no'

- **Name entity**:
        'emb_indv_nm', 'emb_prcs_indv_nm', 
        'indv_prim_first_nm', 'indv_prim_mid_nm', 'indv_prim_lst_nm', 'indv_prim_full_nm', 
        'indv_prim_prcs_first_nm', 'indv_prim_prcs_mid_nm', 'indv_prim_prcs_lst_nm', 'indv_prim_prcs_full_nm',
        'indv_prim_ttl_nm', 'indv_prim_pfx_nm', 'indv_prim_suff_nm', 
        'indv_prim_add_lst_nm', 'indv_scnd_nm',
        'lgl_nm', 'lgl_prcs_nm'
             
- **Gender entity**:  
        'gend_cd'


- **Date of Birth entity**:  
        'cust_dob', 'birth_yr', 'prcs_dob'


- **Government Document entity**:  
        'gov_doc_id'


- **Address entity**:  
        'ad_home_line_care', 'ad_home_st_line1', 'ad_home_st_line2', 'ad_home_st_line3', 'ad_home_st_line4', 
        'ad_home_prcs_st_line1', 'ad_home_prcs_st_line2', 'ad_home_prcs_st_line3', 'ad_home_prcs_st_line4', 
        'ad_home_geo_coord_latd', 'ad_home_geo_coord_longt', 

        'ad_bus_line_care', 'ad_bus_st_line1', 'ad_bus_st_line2', 'ad_bus_st_line3', 'ad_bus_st_line4', 
        'ad_bus_prcs_st_line1', 'ad_bus_prcs_st_line2', 'ad_bus_prcs_st_line3', 'ad_bus_prcs_st_line4', 
        'ad_bus_geo_coord_latd', 'ad_bus_geo_coord_longt', 

        'ad_alt_line_care', 'ad_alt_st_line1', 'ad_alt_st_line2', 'ad_alt_st_line3', 'ad_alt_st_line4', 
        'ad_alt_prcs_st_line1', 'ad_alt_prcs_st_line2', 'ad_alt_prcs_st_line3', 'ad_alt_prcs_st_line4', 
        'ad_alt_geo_coord_latd', 'ad_alt_geo_coord_longt', 

        'ad_temp_line_care', 'ad_temp_st_line1', 'ad_temp_st_line2', 'ad_temp_st_line3', 'ad_temp_st_line4', 
        'ad_temp_prcs_st_line1', 'ad_temp_prcs_st_line2', 'ad_temp_prcs_st_line3', 'ad_temp_prcs_st_line4', 
        'ad_temp_geo_coord_latd', 'ad_temp_geo_coord_longt', 

        'ad_other_line_care', 'ad_other_st_line1', 'ad_other_st_line2', 'ad_other_st_line3', 'ad_other_st_line4', 
        'ad_other_prcs_st_line1', 'ad_other_prcs_st_line2', 'ad_other_prcs_st_line3', 'ad_other_prcs_st_line4', 
        'ad_other_geo_coord_latd', 'ad_other_geo_coord_longt', 

        'ad_add',

 
- **Phone columns**:  
        'home_phone_no', 'home_prcs_phone_no', 'home_prcs_full_phone_no', 
        'alt_home_phone_no', 'alt_home_prcs_phone_no', 'alt_home_prcs_full_phone_no', 

        'bus_phone_no', 'bus_prcs_phone_no', 'bus_prcs_full_phone_no', 
        'alt_bus_phone_no', 'alt_bus_prcs_phone_no', 'alt_bus_prcs_full_phone_no', 

        'mob_phone_no', 'mob_prcs_phone_no', 'mob_prcs_full_phone_no', 
        'alt_mob_phone_no', 'alt_mob_prcs_phone_no', 'alt_mob_prcs_full_phone_no',

        'atty_phone_no', 'atty_prcs_phone_no', 'atty_prcs_full_phone_no', 

        'fax_no', 'prcs_fax_no', 'prcs_full_fax_no', 

        'phone_ani', 

        'other_phone_no', 'other_prcs_phone_no', 'other_prcs_full_phone_no', 

        'add_phone', 
  
- **Email columns**:  
        'srvc_email_ad', 'srvc_prcs_email_ad', 
        'estmt_email_ad', 'estmt_prcs_email_ad', 
        'other_email_ad'
               

<div class="alert alert-info" style="background-color:#006a79; color:white; padding:0px 10px; border-radius:5px;"><h2 style='margin:10px 5px'>Preprocessing</h2>
</div>

**Processing <font color=red>Customer</font> entity**

- Leave **cust_id** for future use.

**Processing <font color=red>Account</font> entity**

In [22]:
cols_account = [
    'acct_id', 'cm11', 'cm13', 'cm15', 'alt_acct_id', 
    'parnt_acct_no', 'mbr_rwrd_id', 'setup_refer_acct_id',
    'bank_prim_acct_no', 'bank_prim_rte_no', 'bank_prim_iban_no',
    'bank_scnd_acct_no', 'bank_scnd_rte_no', 'bank_scnd_iban_no'
]
         
# dm_df[cols_account].head()

In [23]:
width_cm11 = int(dm_df['cm11'].str.encode(encoding='utf-8').str.len().max())
width_cm13 = int(dm_df['cm13'].str.encode(encoding='utf-8').str.len().max())
width_cm15 = int(dm_df['cm15'].str.encode(encoding='utf-8').str.len().max())
width_parnt_acct_no = int(dm_df['parnt_acct_no'].str.encode(encoding='utf-8').str.len().max())

# print(width_cm11)
# print(width_cm13)
# print(width_cm15)
# print(width_parnt_acct_no)

In [24]:
print('Is "acct_id" is a superset of "cm11 ?"', isSubset(dm_df, 'acct_id', 'cm11'))
print('Is "acct_id" is a superset of "cm13 ?"', isSubset(dm_df, 'acct_id', 'cm13'))
print('Is "acct_id" is a superset of "cm15 ?"', isSubset(dm_df, 'acct_id', 'cm15'))
print('Is "acct_id" is a superset of "parnt_acct_no ?"', isSubset(dm_df, 'acct_id', 'parnt_acct_no'))

Is "acct_id" is a superset of "cm11 ?" True
Is "acct_id" is a superset of "cm13 ?" True
Is "acct_id" is a superset of "cm15 ?" True
Is "acct_id" is a superset of "parnt_acct_no ?" True


In [25]:
print('Is "acct_id" is a superset of "parnt_acct_no ?"', isSubset(dm_df, 'acct_id', 'setup_refer_acct_id'))

Is "acct_id" is a superset of "parnt_acct_no ?" False


We notice that the columns viz., **cm11, cm13, cm15 and parnt_acct_no** are subsets of column **acct_id** and can be discarded from futher processing. We also discard **setup_refer_acct_id**.

- It is evident that columns cm11, cm13, cm15 are subsets of acct_id.
- setup_refer_acct_id is a combination of alt_acct_id & parnt_acct_no columns

so they can be removed. Similarly, a glance over other columns shows non demographic columns and so we discard them as well from our dataframe:

In [26]:
# Removing below columns including those that does not belong to demographic information
drop_cols_account = [
    'cm11', 'cm13', 'cm15', 'alt_acct_id', 
    'parnt_acct_no', 'mbr_rwrd_id', 'setup_refer_acct_id',
    'bank_prim_rte_no', 'bank_prim_iban_no',
    'bank_scnd_rte_no', 'bank_scnd_iban_no'
]

print('No. of columns before drop = ', dm_df.shape[1])
dm_df.drop(drop_cols_account, axis=1, inplace=True)
print('No. of columns after drop = ', dm_df.shape[1])

No. of columns before drop =  127
No. of columns after drop =  116


**Processing <font color=red>Name</font> entity**

In [27]:
cols_name = ['emb_indv_nm', 'emb_prcs_indv_nm', 
             'indv_prim_first_nm', 'indv_prim_mid_nm', 'indv_prim_lst_nm', 'indv_prim_full_nm', 
             'indv_prim_prcs_first_nm', 'indv_prim_prcs_mid_nm', 'indv_prim_prcs_lst_nm', 'indv_prim_prcs_full_nm',
             'indv_prim_ttl_nm', 'indv_prim_pfx_nm', 'indv_prim_suff_nm', 
             'indv_prim_add_lst_nm', 'indv_scnd_nm',
             'lgl_nm', 'lgl_prcs_nm']
dm_df[cols_name].head()

emb_indv_nm    emb_prcs_indv_nm indv_prim_first_nm indv_prim_mid_nm  \
0  NaN                 NaN                 MEGAN              NaN               
1  NaN                 NaN                 DAVID              NaN               
2  LAURA PALLAS        LAURA PALLAS        LAURA              NaN               
3  NaN                 NaN                 BERNADETTE         NaN               
4  NARINDER S SAWHNEY  NARINDER S SAWHNEY  NARINDER           S                 

  indv_prim_lst_nm   indv_prim_full_nm indv_prim_prcs_first_nm  \
0  GREEN            MEGAN GREEN         MEGAN                    
1  FLEENER          DAVID FLEENER       DAVID                    
2  PALLAS           LAURA PALLAS        LAURA                    
3  REYNA            BERNADETTE REYNA    BERNADETTE               
4  SAWHNEY          NARINDER S SAWHNEY  NARINDER                 

  indv_prim_prcs_mid_nm indv_prim_prcs_lst_nm indv_prim_prcs_full_nm  \
0  NaN                   GREEN                 MEGAN GREEN             
1  NaN                   FLEENER               DAVID FLEENER           
2  NaN                   PALLAS                LAURA PALLAS            
3  NaN                   REYNA                 BERNADETTE REYNA        
4  S                     SAWHNEY               NARINDER S SAWHNEY      

  indv_prim_ttl_nm indv_prim_pfx_nm indv_prim_suff_nm  indv_prim_add_lst_nm  \
0  NaN              NaN              NaN              NaN                     
1  NaN              NaN              NaN              NaN                     
2  NaN              NaN              NaN              NaN                     
3  NaN              NaN              NaN              NaN                     
4  NaN              NaN              NaN              NaN                     

   indv_scnd_nm           lgl_nm      lgl_prcs_nm  
0 NaN            NaN              NaN              
1 NaN            NaN              NaN              
2 NaN            LOUD BOX ENT     LOUD BOX ENT     
3 NaN            NaN              NaN              
4 NaN            IMPORT BOUTIQUE  IMPORT BOUTIQUE

A glance over the names reveals following details:
- column **emb_prcs_indv_nm** is a processed form of the column **emb_indv_nm**
- column **indv_prim_full_nm** is a concatenated form of the columns **indv_prim_first_nm, indv_prim_mid_nm, indv_prim_lst_nm**
- column **indv_prim_prcs_full_nm** is a processed form of the column **indv_prim_full_nm**
- column **indv_prim_prcs_full_nm** is a concatenated form of the columns **indv_prim_prcs_first_nm, indv_prim_prcs_mid_nm,    indv_prim_prcs_lst_nm**
- column **lgl_prcs_nm** is a processed form of the column **lgl_nm**

Let us take following steps moving further:
- retain only the column **indv_prim_prcs_full_nm** and discard all other columns

In [28]:
dm_df['indv_prim_prcs_full_nm'] = dm_df['indv_prim_prcs_full_nm'].astype(str)
dm_df['indv_prim_prcs_full_nm'] = dm_df['indv_prim_prcs_full_nm'].apply(cleanHumanName)
dm_df['indv_prim_prcs_full_nm'] = dm_df['indv_prim_prcs_full_nm'].str.replace('-', ' ')
dm_df['indv_prim_prcs_full_nm'] = dm_df['indv_prim_prcs_full_nm'].str.lower()

drop_cols_name = [
    'emb_indv_nm', 'emb_prcs_indv_nm', 
    'indv_prim_first_nm', 'indv_prim_mid_nm', 'indv_prim_lst_nm', 'indv_prim_full_nm', 
    'indv_prim_prcs_first_nm', 'indv_prim_prcs_mid_nm', 'indv_prim_prcs_lst_nm', 
    'indv_prim_ttl_nm', 'indv_prim_pfx_nm', 'indv_prim_suff_nm', 
    'indv_prim_add_lst_nm', 'indv_scnd_nm',
    'lgl_nm', 'lgl_prcs_nm'
]

dm_df.drop(columns=drop_cols_name, axis=1, inplace=True)

**Processing <font color=red>Gender</font> entity**

In [29]:
dm_df['gend_cd'].value_counts()

UNKNOWN    7079
MALE       234 
FEMALE     99  
Name: gend_cd, dtype: int64

As we see there are several values of this column are **Unknown**. Though we can use **NLP techniques** to deduce gender code from the names, we revisit this column if need arise. For the time being we discard this column.

In [30]:
drop_cols_gender = ['gend_cd']

# Drop columns
dm_df.drop( columns=drop_cols_gender, axis=1, inplace=True)

**Processing <font color=red>Date of Birth</font> entity**

In [31]:
dm_df[['cust_dob', 'birth_yr', 'prcs_dob']].head()

cust_dob birth_yr    prcs_dob
0  1994-12-18  1994     1994-12-18
1  1972-08-25  1972     1972-08-25
2  1960-08-29  1960     1960-08-29
3  1994-07-09  1994     1994-07-09
4  1938-09-04  1938     1938-09-04

In [32]:
dm_df[['cust_dob', 'prcs_dob']].isnull().sum()

cust_dob    29 
prcs_dob    540
dtype: int64

In [33]:
dm_df['DateOfBirth'] = np.nan

cols_Dob = ['cust_dob', 'prcs_dob']

for col in cols_Dob:
    dm_df['DateOfBirth'].fillna(dm_df[col], inplace=True)

drop_cols_Dob = ['cust_dob', 'prcs_dob', 'birth_yr']

# Drop rows having dates '0001-01-01'
dm_df.drop(dm_df[dm_df['DateOfBirth'] == '0001-01-01'].index, inplace=True)

**Processing <font color=red>Address</font> entity**

In [34]:
# List columns of interest
cols_address = [
    'ad_home_prcs_st_line1', 'ad_home_prcs_st_line2', 'ad_home_prcs_st_line3', 'ad_home_prcs_st_line4', 
    'ad_bus_prcs_st_line1', 'ad_bus_prcs_st_line2', 'ad_bus_prcs_st_line3', 'ad_bus_prcs_st_line4', 
    'ad_alt_prcs_st_line1', 'ad_alt_prcs_st_line2', 'ad_alt_prcs_st_line3', 'ad_alt_prcs_st_line4', 
    'ad_temp_prcs_st_line1', 'ad_temp_prcs_st_line2', 'ad_temp_prcs_st_line3', 'ad_temp_prcs_st_line4',
    'ad_other_prcs_st_line1', 'ad_other_prcs_st_line2', 'ad_other_prcs_st_line3', 'ad_other_prcs_st_line4'
]

cols_lattitude = [
    'ad_home_geo_coord_latd', 
    'ad_bus_geo_coord_latd', 
    'ad_alt_geo_coord_latd', 
    'ad_temp_geo_coord_latd', 
    'ad_other_geo_coord_latd'
    ]

cols_longitude = [
    'ad_home_geo_coord_longt', 
    'ad_bus_geo_coord_longt', 
    'ad_alt_geo_coord_longt', 
    'ad_temp_geo_coord_longt', 
    'ad_other_geo_coord_longt'
    ]

# Create new columns
dm_df['AddressLine'] = np.nan
dm_df['Lattitude'] = np.nan
dm_df['Longitude'] = np.nan

# Combine values into new columns
for address in cols_address:
    dm_df['AddressLine'].fillna(dm_df[address], inplace=True)

for latd in cols_lattitude:
    dm_df['Lattitude'].fillna(dm_df[latd], inplace=True)
    
for lngt in cols_longitude:
    dm_df['Longitude'].fillna(dm_df[lngt], inplace=True)
    

# List unused columns
drop_cols_address_unused = [
    'ad_home_line_care', 'ad_home_st_line1', 'ad_home_st_line2', 'ad_home_st_line3', 'ad_home_st_line4',
    'ad_bus_line_care', 'ad_bus_st_line1', 'ad_bus_st_line2', 'ad_bus_st_line3', 'ad_bus_st_line4',
    'ad_alt_line_care', 'ad_alt_st_line1', 'ad_alt_st_line2', 'ad_alt_st_line3', 'ad_alt_st_line4',
    'ad_temp_line_care', 'ad_temp_st_line1', 'ad_temp_st_line2', 'ad_temp_st_line3', 'ad_temp_st_line4',
    'ad_other_line_care', 'ad_other_st_line1', 'ad_other_st_line2', 'ad_other_st_line3', 'ad_other_st_line4',
    'ad_add' 
]

dm_df.drop(columns=cols_address, axis=1, inplace=True)
dm_df.drop(columns=cols_lattitude, axis=1, inplace=True)
dm_df.drop(columns=cols_longitude, axis=1, inplace=True)
dm_df.drop(columns=drop_cols_address_unused, axis=1, inplace=True)

**Processing <font color=red>Phone</font> entity**

In [35]:
# List columns of interest
cols_phone = [
    'home_phone_no', 'home_prcs_phone_no',
    'home_prcs_full_phone_no', 'alt_home_phone_no', 'alt_home_prcs_phone_no',
    'alt_home_prcs_full_phone_no', 'bus_phone_no', 'bus_prcs_phone_no',
    'bus_prcs_full_phone_no', 'alt_bus_phone_no', 'alt_bus_prcs_phone_no',
    'alt_bus_prcs_full_phone_no', 'mob_phone_no', 'mob_prcs_phone_no', 'mob_prcs_full_phone_no',
    'alt_mob_phone_no', 'alt_mob_prcs_phone_no', 'alt_mob_prcs_full_phone_no',
    'atty_phone_no', 'atty_prcs_phone_no', 'atty_prcs_full_phone_no', 'fax_no', 'prcs_fax_no',
    'prcs_full_fax_no', 'phone_ani', 'other_phone_no', 'other_prcs_phone_no',
    'other_prcs_full_phone_no', 'add_phone'
]

dm_df['CustomerPhone'] = np.nan

for phone in cols_phone:
    dm_df['CustomerPhone'].fillna(dm_df[phone], inplace=True)
    
print('Phone with nulls = ', dm_df['CustomerPhone'].isnull().sum())

dm_df.drop(cols_phone, axis=1, inplace=True)

Phone with nulls =  2465


**Processing <font color=red>Email</font> entity**

In [36]:
dm_df[['srvc_email_ad','srvc_prcs_email_ad','estmt_email_ad','estmt_prcs_email_ad','other_email_ad']].isnull().sum()

srvc_email_ad          5147
srvc_prcs_email_ad     5159
estmt_email_ad         4905
estmt_prcs_email_ad    4922
other_email_ad         7588
dtype: int64

In [37]:
# List columns of interest
cols_emails = ['srvc_email_ad','srvc_prcs_email_ad','estmt_email_ad','estmt_prcs_email_ad','other_email_ad']

dm_df['Email_ID'] = np.nan

for email in cols_emails:
    dm_df['Email_ID'].fillna(dm_df[email], inplace=True)
    
print('Null email values = ', dm_df['Email_ID'].isnull().sum())

dm_df.drop(cols_emails, axis=1, inplace=True)

Null email values =  4613


**Processing <font color=red>Government Document</font> (JSON column)**

In [38]:
# Processing gov_doc_id to fetch Social Security Numbers(SSNs):

df = pd.DataFrame(dm_df['gov_doc_id'])
df.head()

gov_doc_id
0  [{"id":"271980164","typ":"SSN","id_last4":"0164","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2020-01-21T00:00","processed":{"id":"271980164","std_ind":"Y"}}]                                               
1  [{"id":"366061010","typ":"SSN","id_last4":"1010","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2013-11-16T00:00","processed":{"id":"366061010","std_ind":"Y"}}]                                               
2  [{"lst_updt_src":"OTL_CRPS_GNA","processed":{"id":"606947815","std_ind":"E"},"typ":"SSN","id":"606947815","lst_updt_ts":"2014-03-21T13:58:40.946763","id_last4":"7815"}]                                 
3  [{"id":"601432001","typ":"SSN","id_last4":"2001","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2016-11-01T00:00","processed":{"id":"601432001","std_ind":"Y"}}]                                               
4  [{"lst_updt_src":"OTL_CRPS_GNA","processed":{"typ":"SSN","id":"408983148","std_ind":"Y"},"issue_ctry_cd":"AS","typ":"SSN","id":"408983148","lst_updt_ts":"2019-05-04T18:36:00.016348","id_last4":"3148"}]

In [39]:
# Create a column to hold SSNs to be fetched from gov_doc_id

df['ssn_id'] = ''
df.head()

gov_doc_id  \
0  [{"id":"271980164","typ":"SSN","id_last4":"0164","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2020-01-21T00:00","processed":{"id":"271980164","std_ind":"Y"}}]                                                  
1  [{"id":"366061010","typ":"SSN","id_last4":"1010","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2013-11-16T00:00","processed":{"id":"366061010","std_ind":"Y"}}]                                                  
2  [{"lst_updt_src":"OTL_CRPS_GNA","processed":{"id":"606947815","std_ind":"E"},"typ":"SSN","id":"606947815","lst_updt_ts":"2014-03-21T13:58:40.946763","id_last4":"7815"}]                                    
3  [{"id":"601432001","typ":"SSN","id_last4":"2001","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2016-11-01T00:00","processed":{"id":"601432001","std_ind":"Y"}}]                                                  
4  [{"lst_updt_src":"OTL_CRPS_GNA","processed":{"typ":"SSN","id":"408983148","std_ind":"Y"},"issue_ctry_cd":"AS","typ":"SSN","id":"408983148","lst_updt_ts":"2019-05-04T18:36:00.016348","id_last4":"3148"}]   

  ssn_id  
0         
1         
2         
3         
4

In [40]:
# Replace Null values of processed SSNs with the string "Blank Value"
df['gov_doc_id'].fillna('{"processed.id":"Blank Value"}', inplace=True)

In [41]:
df['gov_doc_id'] = df['gov_doc_id'].apply(clean_json)
df['gov_doc_id']

0       [{'id': '271980164', 'typ': 'SSN', 'id_last4': '0164', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2020-01-21T00:00', 'processed': {'id': '271980164', 'std_ind': 'Y'}}]                                                   
1       [{'id': '366061010', 'typ': 'SSN', 'id_last4': '1010', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2013-11-16T00:00', 'processed': {'id': '366061010', 'std_ind': 'Y'}}]                                                   
2       [{'lst_updt_src': 'OTL_CRPS_GNA', 'processed': {'id': '606947815', 'std_ind': 'E'}, 'typ': 'SSN', 'id': '606947815', 'lst_updt_ts': '2014-03-21T13:58:40.946763', 'id_last4': '7815'}]                                     
3       [{'id': '601432001', 'typ': 'SSN', 'id_last4': '2001', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2016-11-01T00:00', 'processed': {'id': '601432001', 'std_ind': 'Y'}}]                                                   
4       [{'lst_updt_src': 'OTL_CRPS_GNA', 'processed': {'typ': 'SSN', 'id': '408983148',

In [42]:
# Check how can we access SSN from the series

pd.json_normalize(df['gov_doc_id'][0])

id  typ id_last4 lst_updt_src       lst_updt_ts processed.id  \
0  271980164  SSN  0164     OTL_CRPS     2020-01-21T00:00  271980164     

  processed.std_ind  
0  Y

In [43]:
pd.json_normalize(df['gov_doc_id'][0])['processed.id']

0    271980164
Name: processed.id, dtype: object

In [44]:
cnt = len(df['gov_doc_id'])
missing_ssd = False
for i in np.arange(cnt):
    try:
        a_row = pd.json_normalize(df['gov_doc_id'][i])['processed.id']
    except:
        missing_ssd = True
    if missing_ssd:
        df['ssn_id'].iloc[i] = 'Missing SSN'
    else:
        missing_ssd = False
        df['ssn_id'].iloc[i] = str(a_row[0])
    #print(i, a_row[0])

In [45]:
df

gov_doc_id  \
0     [{'id': '271980164', 'typ': 'SSN', 'id_last4': '0164', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2020-01-21T00:00', 'processed': {'id': '271980164', 'std_ind': 'Y'}}]                                                      
1     [{'id': '366061010', 'typ': 'SSN', 'id_last4': '1010', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2013-11-16T00:00', 'processed': {'id': '366061010', 'std_ind': 'Y'}}]                                                      
2     [{'lst_updt_src': 'OTL_CRPS_GNA', 'processed': {'id': '606947815', 'std_ind': 'E'}, 'typ': 'SSN', 'id': '606947815', 'lst_updt_ts': '2014-03-21T13:58:40.946763', 'id_last4': '7815'}]                                        
3     [{'id': '601432001', 'typ': 'SSN', 'id_last4': '2001', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2016-11-01T00:00', 'processed': {'id': '601432001', 'std_ind': 'Y'}}]                                                      
4     [{'lst_updt_src': 'OTL_CRPS_GNA', 'processed': {'typ': 'SSN', 'id': '408983148', 'std_ind': 'Y'}, 'issue_ctry_cd': 'AS', 'typ': 'SSN', 'id': '408983148', 'lst_updt_ts': '2019-05-04T18:36:00.016348', 'id_last4': '3148'}]   
...                                                                                                                                                                                                                           ...   
8141  [{'lst_updt_src': 'OTL_CRPS', 'processed': {'typ': 'SSN', 'id': '411732061', 'std_ind': 'Y'}, 'issue_ctry_cd': 'US', 'typ': 'SSN', 'id': '411732061', 'lst_updt_ts': '2017-05-11T15:19:19.137096', 'id_last4': '2061'}]       
8142  [{'id': '261571890', 'typ': 'SSN', 'id_last4': '1890', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2019-04-24T00:00', 'processed': {'id': '261571890', 'std_ind': 'Y'}}]                                                      
8143  [{'id': '466630137', 'typ': 'SSN', 'id_last4': '0137', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2016-01-29T00:00', 'processed': {'id': '466630137', 'std_ind': 'Y'}}]                                                      
8144  [{'id': '442783462', 'typ': 'SSN', 'id_last4': '3462', 'lst_updt_src': 'OTL_CRPS', 'lst_updt_ts': '2016-01-29T00:00', 'processed': {'id': '442783462', 'std_ind': 'Y'}}]                                                      
8145  [{'lst_updt_src': 'OTL_CRPS', 'processed': {'typ': 'SSN', 'id': '057684223', 'std_ind': 'Y'}, 'issue_ctry_cd': 'US', 'typ': 'SSN', 'id': '057684223', 'lst_updt_ts': '2017-08-14T13:26:48.802275', 'id_last4': '4223'}]       

           ssn_id  
0     271980164    
1     366061010    
2     606947815    
3     601432001    
4     408983148    
...         ...    
8141  Missing SSN  
8142  Missing SSN  
8143  Missing SSN  
8144  Missing SSN  
8145  Missing SSN  

[7739 rows x 2 columns]

In [46]:
dm_df['ssn_id'] = df['ssn_id'].astype(str)
dm_df.head()

cust_id        acct_id indv_prim_prcs_full_nm    cust_dob birth_yr  \
0  600125815019  25190699       megan green            1994-12-18  1994      
1  568709454017  975879         david fleener          1972-08-25  1972      
2  360534588017  3727271315801  laura pallas           1960-08-29  1960      
3  196410570010  14884816       bernadette reyna       1994-07-09  1994      
4  35442548013   3798238830600  narinder s sawhney     1938-09-04  1938      

     prcs_dob  \
0  1994-12-18   
1  1972-08-25   
2  1960-08-29   
3  1994-07-09   
4  1938-09-04   

                                                                                                                                                                                                  gov_doc_id  \
0  [{"id":"271980164","typ":"SSN","id_last4":"0164","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2020-01-21T00:00","processed":{"id":"271980164","std_ind":"Y"}}]                                                  
1  [{"id":"366061010","typ":"SSN","id_last4":"1010","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2013-11-16T00:00","processed":{"id":"366061010","std_ind":"Y"}}]                                                  
2  [{"lst_updt_src":"OTL_CRPS_GNA","processed":{"id":"606947815","std_ind":"E"},"typ":"SSN","id":"606947815","lst_updt_ts":"2014-03-21T13:58:40.946763","id_last4":"7815"}]                                    
3  [{"id":"601432001","typ":"SSN","id_last4":"2001","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2016-11-01T00:00","processed":{"id":"601432001","std_ind":"Y"}}]                                                  
4  [{"lst_updt_src":"OTL_CRPS_GNA","processed":{"typ":"SSN","id":"408983148","std_ind":"Y"},"issue_ctry_cd":"AS","typ":"SSN","id":"408983148","lst_updt_ts":"2019-05-04T18:36:00.016348","id_last4":"3148"}]   

   bank_prim_acct_no  bank_scnd_acct_no DateOfBirth           AddressLine  \
0 NaN                NaN                 1994-12-18  8413 E STREET          
1 NaN                NaN                 1972-08-25  10190 N 600 E          
2 NaN                NaN                 1960-08-29  11559 DONA TERESA DR   
3 NaN                NaN                 1994-07-09  1010 S 1ST STREET      
4 NaN                NaN                 1938-09-04  5601 CLOVERMEADE DR    

   Lattitude  Longitude CustomerPhone Email_ID     ssn_id  
0 NaN        NaN         NaN           NaN      271980164  
1 NaN        NaN         8123713733    NaN      366061010  
2 NaN        NaN         NaN           NaN      606947815  
3 NaN        NaN         6234998313    NaN      601432001  
4 NaN        NaN         6153731643    NaN      408983148

In [47]:
dm_df.drop(['gov_doc_id'], axis=1, inplace=True)

In [48]:
dm_df.head()

cust_id        acct_id indv_prim_prcs_full_nm    cust_dob birth_yr  \
0  600125815019  25190699       megan green            1994-12-18  1994      
1  568709454017  975879         david fleener          1972-08-25  1972      
2  360534588017  3727271315801  laura pallas           1960-08-29  1960      
3  196410570010  14884816       bernadette reyna       1994-07-09  1994      
4  35442548013   3798238830600  narinder s sawhney     1938-09-04  1938      

     prcs_dob  bank_prim_acct_no  bank_scnd_acct_no DateOfBirth  \
0  1994-12-18 NaN                NaN                 1994-12-18   
1  1972-08-25 NaN                NaN                 1972-08-25   
2  1960-08-29 NaN                NaN                 1960-08-29   
3  1994-07-09 NaN                NaN                 1994-07-09   
4  1938-09-04 NaN                NaN                 1938-09-04   

            AddressLine  Lattitude  Longitude CustomerPhone Email_ID  \
0  8413 E STREET        NaN        NaN         NaN           NaN       
1  10190 N 600 E        NaN        NaN         8123713733    NaN       
2  11559 DONA TERESA DR NaN        NaN         NaN           NaN       
3  1010 S 1ST STREET    NaN        NaN         6234998313    NaN       
4  5601 CLOVERMEADE DR  NaN        NaN         6153731643    NaN       

      ssn_id  
0  271980164  
1  366061010  
2  606947815  
3  601432001  
4  408983148

In [49]:
tbl_results = getNullStats(dm_df)
tbl_results

Total Features(Columns) of dataset =  15
Null Features(Columns) of dataset =  11


Nulls  Percent
bank_prim_acct_no  7739   100.00 
bank_scnd_acct_no  7739   100.00 
Lattitude          7739   100.00 
Longitude          7739   100.00 
Email_ID           4613   59.61  
CustomerPhone      2465   31.85  
birth_yr           133    1.72   
prcs_dob           133    1.72   
AddressLine        128    1.65   
cust_dob           29     0.37   
DateOfBirth        29     0.37

There are several columns with 100% nulls, which add no contribution to our findings. So let us discard all such columns.

In [50]:
threshold = 80

# Collect columns with 80 % null values
cols_insignificant = tbl_results[tbl_results['Percent'] >= threshold].index.to_list()

total_cols = len(dm_df.columns)
cnt_insignificant_cols = len(cols_insignificant)

print('There are', cnt_insignificant_cols, 'columns with null values out of ', total_cols)
print('We are left with ', total_cols - cnt_insignificant_cols, 'columns.\n')

# Dropping insignificant columns
dm_df.drop(cols_insignificant, axis=1, inplace=True)

print('We have removed following insignificant columns:')
for col in cols_insignificant:
    print(col)
    
print('\nWe are left with following columns:')
for col in dm_df.columns:
    print(col)

There are 4 columns with null values out of  15
We are left with  11 columns.

We have removed following insignificant columns:
bank_prim_acct_no
bank_scnd_acct_no
Lattitude
Longitude

We are left with following columns:
cust_id
acct_id
indv_prim_prcs_full_nm
cust_dob
birth_yr
prcs_dob
DateOfBirth
AddressLine
CustomerPhone
Email_ID
ssn_id


In [51]:
dm_df.head()

cust_id        acct_id indv_prim_prcs_full_nm    cust_dob birth_yr  \
0  600125815019  25190699       megan green            1994-12-18  1994      
1  568709454017  975879         david fleener          1972-08-25  1972      
2  360534588017  3727271315801  laura pallas           1960-08-29  1960      
3  196410570010  14884816       bernadette reyna       1994-07-09  1994      
4  35442548013   3798238830600  narinder s sawhney     1938-09-04  1938      

     prcs_dob DateOfBirth           AddressLine CustomerPhone Email_ID  \
0  1994-12-18  1994-12-18  8413 E STREET         NaN           NaN       
1  1972-08-25  1972-08-25  10190 N 600 E         8123713733    NaN       
2  1960-08-29  1960-08-29  11559 DONA TERESA DR  NaN           NaN       
3  1994-07-09  1994-07-09  1010 S 1ST STREET     6234998313    NaN       
4  1938-09-04  1938-09-04  5601 CLOVERMEADE DR   6153731643    NaN       

      ssn_id  
0  271980164  
1  366061010  
2  606947815  
3  601432001  
4  408983148

In [52]:
dm_df.isnull().sum()

cust_id                   0   
acct_id                   0   
indv_prim_prcs_full_nm    0   
cust_dob                  29  
birth_yr                  133 
prcs_dob                  133 
DateOfBirth               29  
AddressLine               128 
CustomerPhone             2465
Email_ID                  4613
ssn_id                    0   
dtype: int64

In [53]:
dm_df[dm_df.notnull()]

cust_id        acct_id indv_prim_prcs_full_nm    cust_dob birth_yr  \
0     600125815019  25190699       megan green            1994-12-18  1994      
1     568709454017  975879         david fleener          1972-08-25  1972      
2     360534588017  3727271315801  laura pallas           1960-08-29  1960      
3     196410570010  14884816       bernadette reyna       1994-07-09  1994      
4     35442548013   3798238830600  narinder s sawhney     1938-09-04  1938      
...           ...             ...                 ...            ...   ...      
8141  855386850019  3712984222700  nina appareddy         1992-01-28  1992      
8142  355336297011  23818556       scott malone           1973-11-25  1973      
8143  634029714018  12536775       thomas moore           1983-08-08  1983      
8144  620277640017  12534539       austin chase           1971-02-19  1971      
8145  701177811014  3798228893900  moshe schwartz         1983-07-14  1983      

        prcs_dob DateOfBirth              AddressLine CustomerPhone  \
0     1994-12-18  1994-12-18  8413 E STREET            NaN            
1     1972-08-25  1972-08-25  10190 N 600 E            8123713733     
2     1960-08-29  1960-08-29  11559 DONA TERESA DR     NaN            
3     1994-07-09  1994-07-09  1010 S 1ST STREET        6234998313     
4     1938-09-04  1938-09-04  5601 CLOVERMEADE DR      6153731643     
...          ...         ...                  ...             ...     
8141  1992-01-28  1992-01-28  9219 ROYAL MOUNTAIN DR   4238555965     
8142  1973-11-25  1973-11-25  5320 FORT CAROLINE ROAD  NaN            
8143  1983-08-08  1983-08-08  6235 HIGHWAY 36          9798241205     
8144  1971-02-19  1971-02-19  41 PEABODY STREET        3109277361     
8145  1983-07-14  1983-07-14  570 WHYTHE AVE           7184866217     

                   Email_ID       ssn_id  
0     NaN                    271980164    
1     NaN                    366061010    
2     NaN                    606947815    
3     NaN                    601432001    
4     NaN                    408983148    
...   ...                          ...    
8141  nina@ramtec.com        Missing SSN  
8142  NaN                    Missing SSN  
8143  NaN                    Missing SSN  
8144  NaN                    Missing SSN  
8145  moishunited@yahoo.com  Missing SSN  

[7739 rows x 11 columns]

In [54]:
dm_df.dropna(axis=0, inplace=True)

In [55]:
dm_df[dm_df.notnull()]

cust_id          acct_id indv_prim_prcs_full_nm    cust_dob  \
6     11351714014   3725517067300    elizabeth s hutten     1964-09-30   
8     269872999012  3725374672002    jigar r patel          1976-01-01   
9     690307044012  1517919476       robert p brooks        1942-04-02   
12    19489139017   3782091487036    steve bauerfeind       1968-10-01   
13    770974190017  3767869038700    timothy j hilgert      1988-08-02   
...            ...            ...                  ...             ...   
8131  770974190017  3727286478300    timothy j hilgert      1988-08-02   
8134  528416283012  3792599838400    xin fan                1985-07-14   
8137  736509012017  373794006545781  nemil vora             1989-08-10   
8141  855386850019  3712984222700    nina appareddy         1992-01-28   
8145  701177811014  3798228893900    moshe schwartz         1983-07-14   

     birth_yr    prcs_dob DateOfBirth             AddressLine  \
6     1964     1964-09-30  1964-09-30  30 TUCSON CIR            
8     1976     1976-01-01  1976-01-01  520 S EWING AVE          
9     1942     1942-04-02  1942-04-02  28561 LA CUMBRE          
12    1968     1968-10-01  1968-10-01  1923 N GRAMERCY PL       
13    1988     1988-08-02  1988-08-02  503 S HENRY ST           
...    ...            ...         ...             ...           
8131  1988     1988-08-02  1988-08-02  503 S HENRY ST           
8134  1985     1985-07-14  1985-07-14  7455 BLYTHE PL           
8137  1989     1989-08-10  1989-08-10  281 KIRK AVE             
8141  1992     1992-01-28  1992-01-28  9219 ROYAL MOUNTAIN DR   
8145  1983     1983-07-14  1983-07-14  570 WHYTHE AVE           

                                                                                                                                                                                                       CustomerPhone  \
6     4156095922                                                                                                                                                                                                       
8     [{"lst_updt_src":"OTL_CRPS","processed":{"ctry_cd":"+1","full_nbr":"+12143881014","nbr":"2143881014","std_ind":"Y"},"lst_updt_ts":"2009-01-25T00:00","device_typ":"LANDLINE","ctc_cd":"V","nbr":"2143881014"}]   
9     9496062641                                                                                                                                                                                                       
12    3104958286                                                                                                                                                                                                       
13    2296300267                                                                                                                                                                                                       
...          ...                                                                                                                                                                                                       
8131  2296300267                                                                                                                                                                                                       
8134  9519618529                                                                                                                                                                                                       
8137  4088352179                                                                                                                                                                                                       
8141  4238555965                                                                                                                                                                     

In [56]:
dm_df.isnull().sum()

cust_id                   0
acct_id                   0
indv_prim_prcs_full_nm    0
cust_dob                  0
birth_yr                  0
prcs_dob                  0
DateOfBirth               0
AddressLine               0
CustomerPhone             0
Email_ID                  0
ssn_id                    0
dtype: int64

In [57]:
len(dm_df)

2708

In [58]:
pd.set_option('display.max_rows', None)

In [59]:
cols_final = ['indv_prim_prcs_full_nm', 'DateOfBirth', 'acct_id', 'cust_id', 'ssn_id', 'AddressLine', 'CustomerPhone', 'Email_ID']
dm_df_sorted = dm_df[cols_final].sort_values(['indv_prim_prcs_full_nm', 'DateOfBirth', 'acct_id', 'cust_id'])
# dm_df_sorted

In [60]:
pd.set_option('display.max_rows', 10)

In [61]:
cntCustomers = len(dm_df_sorted['cust_id'].unique())
print('There are ', cntCustomers, 'customers in the current data set.')

There are  631 customers in the current data set.


<font color=red>**Study the issues in the existing data**</font>

1) Different customers having same name but 
- different customer ids
- different dates of birth, same year, same month

Question: 
- Can we safely treat as two different customers ?

Remarks:
- Should we weight features or consider equal probability of errors on all features and sum up to take further course of action

In [62]:
dm_df[dm_df['indv_prim_prcs_full_nm'] == 'alejandra p madrid']

cust_id        acct_id indv_prim_prcs_full_nm    cust_dob birth_yr  \
6935  52324565013   3717345006700  alejandra p madrid     1975-04-19  1975      
7013  402904311019  3739557393000  alejandra p madrid     1975-04-01  1975      

        prcs_dob DateOfBirth         AddressLine CustomerPhone  \
6935  1975-04-19  1975-04-19  13484 NW 13TH ST    9542966916     
7013  1975-04-01  1975-04-01  11302 ROUNDELAY RD  9544415961     

                            Email_ID       ssn_id  
6935  alespalding@gmail.com           Missing SSN  
7013  cargoconnectionc@bellsouth.net  Missing SSN

2) Same customer having 
- different parts of names
- different dates of birth

Remarks:
- We might have to take 
  - elementary form of name (last name, first name, middle name)
  - split date of birth to date, month, year
 
 We might end up having lots of features.

In [63]:
dm_df[dm_df['indv_prim_prcs_full_nm'].isin(['ABBY M PLOTKA', 'ABBY PLOTKA'])]

Empty DataFrame
Columns: [cust_id, acct_id, indv_prim_prcs_full_nm, cust_dob, birth_yr, prcs_dob, DateOfBirth, AddressLine, CustomerPhone, Email_ID, ssn_id]
Index: []

3) 

..

4)

..

<div class="alert alert-info" style="background-color:#006a79; color:white; padding:0px 10px; border-radius:5px;"><h2 style='margin:10px 5px'>Clustering</h2>
</div>

In [64]:
nRows = len(dm_df_sorted)
# nRows = 500

df_dm_partial = dm_df_sorted[:nRows]
df_dm_partial['acct_id'].astype(str)

df_dm_partial['customer'] = df_dm_partial['indv_prim_prcs_full_nm']
df_dm_partial.head()

indv_prim_prcs_full_nm DateOfBirth        acct_id      cust_id  \
7190  abby m plotka          1958-01-31  3791416090600  27819937015   
1431  abby plotka            1958-01-31  3713031691300  27819937015   
3757  abby plotka            1958-01-31  3728224493701  27819937015   
7617  abby plotka            1958-01-31  3792795329700  27819937015   
1518  abby plotka            1958-01-31  3798011106300  27819937015   

           ssn_id              AddressLine  \
7190  Missing SSN  369 HERITAGE HLS          
1431  Missing SSN  369 HERITAGE HLS          
3757  Missing SSN  369 HERITAGE HLS UNIT D   
7617  Missing SSN  369 HERITAGE HLS          
1518  Missing SSN  369 HERITAGE HLS          

                                                                                                                                                                                                       CustomerPhone  \
7190  9172821150                                                                                                                                                                                                       
1431  9146698189                                                                                                                                                                                                       
3757  [{"nbr":"9146698189","ctc_cd":"V","device_typ":"LANDLINE","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2010-04-04T00:00","processed":{"nbr":"9146698189","ctry_cd":"+1","full_nbr":"+19146698189","std_ind":"Y"}}]   
7617  9172821150                                                                                                                                                                                                       
1518  9172821150                                                                                                                                                                                                       

                     Email_ID       customer  
7190  amazing2@optonline.net   abby m plotka  
1431  amazing2@optonline.net   abby plotka    
3757  amazing10@optonline.com  abby plotka    
7617  amazing2@optonline.net   abby plotka    
1518  amazing2@optonline.net   abby plotka

In [65]:
# To capture only mail id leaving the domain details for better capture of e-mail clusters
# df_dm_partial['Email_ID'] = df_dm_partial['Email_ID'].apply(lambda x: "".join(re.split("[^a-zA-Z]*", x.split('@')[0])))

In [66]:
# Show accounts of each customer, graphically

# fig, ax = plt.subplots(figsize=(20, 30))
# x_tick_angle = 90
# plt.xticks(rotation=x_tick_angle)

# sns.scatterplot(data=df_dm_partial, x="indv_prim_prcs_full_nm", y=df_dm_partial['acct_id'].astype(str))

In [67]:
df_dm_partial['indv_prim_prcs_full_nm'] = df_dm_partial.loc[:, 'indv_prim_prcs_full_nm'].str.lower()
df_dm_partial['cust_id'] = df_dm_partial.loc[:, 'cust_id'].astype('str')

In [68]:
# Convert unicode characters to ascii and chop-off special characters
df_dm_partial['indv_prim_prcs_full_nm'] = df_dm_partial['indv_prim_prcs_full_nm'].apply(normalize_unicode_to_ascii)

In [69]:
df_dm_partial['Email_ID'] = df_dm_partial['Email_ID'].apply(getMailIDs)

In [70]:
df_dm_partial[['indv_prim_prcs_full_nm', 'cust_id', 'acct_id', 'DateOfBirth', 'Email_ID']].head()

indv_prim_prcs_full_nm      cust_id        acct_id DateOfBirth Email_ID
7190  abby m plotka          27819937015  3791416090600  1958-01-31  amazing
1431  abby plotka            27819937015  3713031691300  1958-01-31  amazing
3757  abby plotka            27819937015  3728224493701  1958-01-31  amazing
7617  abby plotka            27819937015  3792795329700  1958-01-31  amazing
1518  abby plotka            27819937015  3798011106300  1958-01-31  amazing

<div class="alert alert-info" style="background-color:#006a79; color:white; padding:0px 10px; border-radius:5px;"><h2 style='margin:10px 5px'>Vectorization</h2>
</div>

**Vectorizing <font color=red>Name</font>**

In [71]:
# Find maximum words in the column 'indv_prim_prcs_full_nm'
max_words_name = np.max([len(x.split()) for x in df_dm_partial['indv_prim_prcs_full_nm'].tolist()])

tfidf_Name_vector = TfidfVectorizer(max_df=0.999999999, 
                                   max_features=200000,
                                   min_df=0.000000001, 
                                   stop_words='english',
                                   use_idf=False, 
                                   tokenizer=getAllPermutations, 
                                   ngram_range=(1, max_words_name))

%time tfidf_name_matrix = tfidf_Name_vector.fit_transform(df_dm_partial['indv_prim_prcs_full_nm'])

# print(tfidf_name_matrix.shape)
tfidf_name_matrix

features = tfidf_Name_vector.get_feature_names()
# print(len(features))
# features

corpus = [n for n in df_dm_partial['indv_prim_prcs_full_nm']]
# print(len(corpus))
# corpus

df_name = pd.DataFrame(tfidf_name_matrix.todense(), index=corpus, columns=features)
df_name.head()

Wall time: 234 ms


2nd  2nd cassell  2nd cassell churchill  \
abby m plotka  0.0  0.0          0.0                     
abby plotka    0.0  0.0          0.0                     
abby plotka    0.0  0.0          0.0                     
abby plotka    0.0  0.0          0.0                     
abby plotka    0.0  0.0          0.0                     

               2nd cassell churchill cassell 2nd  \
abby m plotka  0.0                                 
abby plotka    0.0                                 
abby plotka    0.0                                 
abby plotka    0.0                                 
abby plotka    0.0                                 

               2nd cassell churchill cassell 2nd churchill 2nd cassell  \
abby m plotka  0.0                                                       
abby plotka    0.0                                                       
abby plotka    0.0                                                       
abby plotka    0.0                                                       
abby plotka    0.0                                                       

               2nd cassell churchill cassell 2nd churchill 2nd cassell cassell churchill 2nd  \
abby m plotka  0.0                                                                             
abby plotka    0.0                                                                             
abby plotka    0.0                                                                             
abby plotka    0.0                                                                             
abby plotka    0.0                                                                             

               2nd cassell churchill cassell 2nd churchill 2nd cassell cassell churchill 2nd cassell 2nd churchill  \
abby m plotka  0.0                                                                                                   
abby plotka    0.0                                                                                                   
abby plotka    0.0                                                                                                   
abby plotka    0.0                                                                                                   
abby plotka    0.0                                                                                                   

               2nd churchill  2nd churchill 2nd cassell  \
abby m plotka  0.0            0.0                         
abby plotka    0.0            0.0                         
abby plotka    0.0            0.0                         
abby plotka    0.0            0.0                         
abby plotka    0.0            0.0                         

               2nd churchill 2nd cassell churchill cassell 2nd  ...  \
abby m plotka  0.0                                              ...   
abby plotka    0.0                                              ...   
abby plotka    0.0                                              ...   
abby plotka    0.0                                              ...   
abby plotka    0.0                                              ...   

               zheng vincent zheng zheng vincent  zhenhua  zhenhua huang  \
abby m plotka  0.0                                0.0      0.0             
abby plotka    0.0                                0.0      0.0             
abby plotka    0.0                                0.0      0.0             
abby plotka    0.0                                0.0      0.0             
abby plotka    0.0                                0.0      0.0             

               zhenhua huang huang zhenhua  zhenhua huang zhenhua huang  \
abby m plotka  0.0                          0.0                           
abby plotka    0.0                          0.0                           
abby plotka    0.0                          0.0                           
abby plotka    0.0                          0.0                           
abby plo

**Vectorizing <font color=red>Date of Birth</font>**

In [72]:
%time tfidf_Dob_matrix, df_Dob = Vectorize(df_dm_partial, 'DateOfBirth', False)
df_Dob.head()

Shape of the matrix => (2708, 98)
No. of Features => 98
No. of documents => 2708
Wall time: 24 ms


01   02   03   04   05   06   07   08   09   10  ...   22  \
1958-01-31  0.371963  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1958-01-31  0.371963  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1958-01-31  0.371963  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1958-01-31  0.371963  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   
1958-01-31  0.371963  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0   

             23   24   25   26   27   28   29   30        31  
1958-01-31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.664236  
1958-01-31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.664236  
1958-01-31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.664236  
1958-01-31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.664236  
1958-01-31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.664236  

[5 rows x 98 columns]

**Vectorizing <font color=red>SSN</font>** <font color=red>(See the behavior by not considering it)</font>

**Vectorizing <font color=red>Customer Phone</font>**

**Vectorizing <font color=red>Address</font>**

**Vectorizing <font color=red>Email ID</font>**

<div class="alert alert-info" style="background-color:#006a79; color:white; padding:0px 10px; border-radius:5px;"><h2 style='margin:10px 5px'>Start Clustering (Cosine Similarity)</h2>
</div>

## Cosine Similarity in Comment State

## K-means Clustering

<div class="alert alert-info" style="background-color:#006a79; color:white; padding:0px 10px; border-radius:5px;"><h2 style='margin:10px 5px'>Start Clustering (K-means)</h2>
</div>

In [73]:
num_clusters = len(df_dm_partial['cust_id'].unique())

km_name = kMeansClustering(tfidf_name_matrix, num_clusters)
km_Dob = kMeansClustering(tfidf_Dob_matrix, num_clusters)
# km_SSN = kMeansClustering(tfidf_SSN_matrix, num_clusters)
# km_Phone = kMeansClustering(tfidf_Phone_matrix, num_clusters)
# km_Address = kMeansClustering(tfidf_Address_matrix, num_clusters)
# km_Email = kMeansClustering(tfidf_Email_matrix, num_clusters)

clusters_name = km_name.labels_.tolist()
clusters_Dob = km_Dob.labels_.tolist()
# clusters_SSN = km_SSN.labels_.tolist()
# clusters_Phone = km_Phone.labels_.tolist()
# clusters_Address = km_Address.labels_.tolist()
# clusters_Email = km_Email.labels_.tolist()

# clusters_name
# clusters_Dob
## clusters_SSN
# clusters_Phone
# clusters_Addr
# clusters_Email

# print('Name clusters =>', len(clusters_name))
# print(len('Date of birth clusters =>', clusters_Dob))
## print('Name clusters =>', len(clusters_SSN))
# print('Phone clusters =>', len(clusters_Phone))
# print('Address clusters =>', len(clusters_Address))
# print('Email clusters =>', len(clusters_Email))

Wall time: 17.4 s
Wall time: 1min 48s


**Clustering <font color=red>Clusters</font>**

(All the independent features viz., Name, Date of birth, Phone, Address, Email ID refer to identify customer uniquely)

In [74]:
num_clusters = len(df_dm_partial['cust_id'].unique())
ndigits = len(str(num_clusters+1))
print('Digits in maximum clusters formed =>', ndigits)

Digits in maximum clusters formed => 3


In [75]:
df_dm_partial['cluster by name']    = list(map(lambda x: str(x).zfill(ndigits), clusters_name))
df_dm_partial['cluster by Dob']     = list(map(lambda x: str(x).zfill(ndigits), clusters_Dob))
# df_dm_partial['cluster by SSN']     = list(map(lambda x: str(x).zfill(ndigits), clusters_SSN))
# df_dm_partial['cluster by Phone']   = list(map(lambda x: str(x).zfill(ndigits), clusters_Phone))
# df_dm_partial['cluster by Address'] = list(map(lambda x: str(x).zfill(ndigits), clusters_Address))
# df_dm_partial['cluster by Email']   = list(map(lambda x: str(x).zfill(ndigits), clusters_Email))

In [76]:
df_dm_partial['cluster by clusters'] = ('N' + df_dm_partial['cluster by name'].astype(str) 
                                + ' ' + 'D' + df_dm_partial['cluster by Dob'].astype(str))
#                                + ' ' + df_dm_partial['cluster by SSN'].astype(str)
#                                 + ' ' + 'P' + df_dm_partial['cluster by Phone'].astype(str)
#                                 + ' ' + 'A' + df_dm_partial['cluster by Address'].astype(str)
#                                 + ' ' + 'E' + df_dm_partial['cluster by Email'].astype(str))

In [77]:
df_dm_partial.head()

indv_prim_prcs_full_nm DateOfBirth        acct_id      cust_id  \
7190  abby m plotka          1958-01-31  3791416090600  27819937015   
1431  abby plotka            1958-01-31  3713031691300  27819937015   
3757  abby plotka            1958-01-31  3728224493701  27819937015   
7617  abby plotka            1958-01-31  3792795329700  27819937015   
1518  abby plotka            1958-01-31  3798011106300  27819937015   

           ssn_id              AddressLine  \
7190  Missing SSN  369 HERITAGE HLS          
1431  Missing SSN  369 HERITAGE HLS          
3757  Missing SSN  369 HERITAGE HLS UNIT D   
7617  Missing SSN  369 HERITAGE HLS          
1518  Missing SSN  369 HERITAGE HLS          

                                                                                                                                                                                                       CustomerPhone  \
7190  9172821150                                                                                                                                                                                                       
1431  9146698189                                                                                                                                                                                                       
3757  [{"nbr":"9146698189","ctc_cd":"V","device_typ":"LANDLINE","lst_updt_src":"OTL_CRPS","lst_updt_ts":"2010-04-04T00:00","processed":{"nbr":"9146698189","ctry_cd":"+1","full_nbr":"+19146698189","std_ind":"Y"}}]   
7617  9172821150                                                                                                                                                                                                       
1518  9172821150                                                                                                                                                                                                       

     Email_ID       customer cluster by name cluster by Dob  \
7190  amazing  abby m plotka  092             017             
1431  amazing  abby plotka    092             017             
3757  amazing  abby plotka    092             017             
7617  amazing  abby plotka    092             017             
1518  amazing  abby plotka    092             017             

     cluster by clusters  
7190  N092 D017           
1431  N092 D017           
3757  N092 D017           
7617  N092 D017           
1518  N092 D017

**Vectorizing <font color=red>Individual Clusters</font>**

In [78]:
tfidf_IndCluster_vector = TfidfVectorizer(max_df=0.999999999, 
                                           max_features=200000,
                                           min_df=0.000000001, 
                                           use_idf=True) 


%time tfidf_IndCluster_matrix = tfidf_IndCluster_vector.fit_transform(df_dm_partial['cluster by clusters'])

print(tfidf_IndCluster_matrix.shape)
tfidf_IndCluster_matrix

Wall time: 45.7 ms
(2708, 1249)


<2708x1249 sparse matrix of type '<class 'numpy.float64'>'
	with 5416 stored elements in Compressed Sparse Row format>

In [79]:
features = tfidf_IndCluster_vector.get_feature_names()
# print(len(features))
# features

In [80]:
corpus = [n for n in df_dm_partial['cluster by clusters']]
# print(len(corpus))
# corpus

In [81]:
df_IndCluster = pd.DataFrame(tfidf_IndCluster_matrix.todense(), index=corpus, columns=features)

**Clustering <font color=red> clusters</font>** 

(Clustering clusters formed by independent features)

In [82]:
# Apply k-means clustering on 'Cluster by clusters'

num_clusters = len(df_dm_partial['cust_id'].unique())
km_IndCluster = kMeansClustering(tfidf_IndCluster_matrix, num_clusters)
clusters_IndCluster = km_IndCluster.labels_.tolist()

Wall time: 11.5 s


In [83]:
print(len(clusters_IndCluster))
# clusters_IndCluster

2708


<div class="alert alert-info" style="background-color:#006a79; color:white; padding:0px 10px; border-radius:5px;"><h2 style='margin:10px 5px'>Show Final results</h2>
</div>

In [84]:
customers = df_dm_partial.loc[:, 'customer'].str.lower()[:nRows].tolist()
dobs = df_dm_partial.loc[:, 'DateOfBirth'].str[:].tolist()
cust_ids = df_dm_partial.loc[:, 'cust_id'].str[:].tolist()
# SSNs = df_dm_partial.loc[:, 'ssn_id'].str[:].tolist()
# Phones = df_dm_partial.loc[:, 'CustomerPhone'].str[:].tolist()
# Addresses = df_dm_partial.loc[:, 'AddressLine'].str[:].tolist()
# Emails = df_dm_partial.loc[:, 'Email_ID'].str[:].tolist()

# print(len(customers))
# print(len(dobs))
# print(len(cust_ids))
# print(len(SSNs))
# print(len(Phones))
# print(len(Addresses))
# print(len(Emails))

# customers
# dobs
# cust_ids
# # SSNs
# # Phones
# # Addresses
# # Emails

In [85]:
import pandas as pd

amex_dict = {'customer': customers, 
             'birth date' : dobs, 
             'cust ID' : cust_ids, 
             'cluster by name' : clusters_name, 
             'cluster by Dob' : clusters_Dob, 
#             'cluster by SSN' : clusters_SSN, 
#              'cluster by Phone' : clusters_Phone, 
#              'cluster by Address' : clusters_Address, 
#              'cluster by Email' : clusters_Email,
             'cluster by Clusters' : clusters_IndCluster}

amex_frame = pd.DataFrame(amex_dict, 
                          index=[clusters_name], 
                          columns = ['customer', 'birth date', 'cust ID', 'cluster by name', 'cluster by Dob', 
#                                     'cluster by SSN', 'cluster by Phone', 
#                                     'cluster by Dob', 'cluster by Phone', 
#                                      'cluster by Address', 'cluster by Email', 
                                     'cluster by Clusters'])

In [86]:
amex_frame.to_csv('Data/km_clusters_info.csv', index=True)

In [87]:
pd.set_option('display.max_rows', None)
# amex_frame.sort_values(by=['cluster by name']);

**Present results in color for easy glance**

In [88]:
amx = amex_frame.sort_values(by=['cluster by name'])

In [89]:
amx.reset_index(drop=True, inplace=True)
# amx

In [90]:
def highlight_alternate_rows(s, column):
    is_max = pd.Series(data=False, index=s.index)
    is_max[column] = s.loc[column] % 2
    return ['color: red' if is_max.any() else 'color: blue' for v in is_max]

In [91]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
amx.style.apply(highlight_alternate_rows, column='cluster by name', axis=1)

In [92]:
pd.reset_option('display.max_rows')
pd.reset_option('display.max_columns')

## **Trials**

## **Get clusters having <font color=red>multiple cust_ids</font>**